In [1]:
%load_ext sql
%sql sqlite:///CourseDataWarehouse.db

'Connected: @CourseDataWarehouse.db'

In [2]:
%%sql
ATTACH 'DWETL.db' AS CDDB

 * sqlite:///CourseDataWarehouse.db
Done.


[]

In [3]:
%%sql
select * from CDDB.PROGRAMS LIMIT 1

 * sqlite:///CourseDataWarehouse.db
Done.


[(1, 'AN', 'Asian Studies')]

In [4]:
%%sql

DROP TABLE IF EXISTS PROGRAMS_DIM;
DROP TABLE IF EXISTS LOCATIONS_DIM;
DROP TABLE IF EXISTS TIMES_DIM;
DROP TABLE IF EXISTS FACULTY_DIM;
DROP TABLE IF EXISTS COURSE_CATALOGS_DIM;
DROP TABLE IF EXISTS COURSES_FACT;





vacuum; 

CREATE TABLE PROGRAMS_DIM (
    PID INTEGER NOT NULL PRIMARY KEY,
    program_code TEXT NOT NULL,
    program_name TEXT NOT NULL
);


CREATE TABLE LOCATIONS_DIM (
    LID INTEGER PRIMARY KEY,
    location TEXT ,
    BuildingName TEXT

);


CREATE TABLE FACULTY_DIM (
    FID  INTEGER NOT NULL PRIMARY KEY,
    instructor_fname TEXT NOT NULL,
    instructor_lname TEXT NOT NULL
);


CREATE TABLE COURSE_CATALOGS_DIM (
    CID INTEGER PRIMARY KEY,
    Catalog_ID TEXT NOT NULL,
    Credits TEXT  NULL,
    Prereqs TEXT,
    Coreqs TEXT,
    Fees INTEGER,
    Description TEXT,
    Attributes TEXT
);



CREATE TABLE COURSES_FACT (
    CID INTEGER NULL ,
    CRN INTEGER NOT NULL,
    SEMESTER TEXT NOT NULL ,
    YEAR INTEGER NOT NULL,
    Title TEXT  NULL,
    SECTION TEXT NOT NULL,
    Act INTEGER,
    Cap INTEGER,
    Rem INTEGER, 
    timecodes TEXT,
    PID INTEGER  NULL,
    LID INTEGER  NULL,
    FID INTEGER  NULL,
   Catalog_ID  TEXT NULL ,
    FOREIGN KEY (PID) REFERENCES PROGRAMS_DIM (PID),
    FOREIGN KEY (LID) REFERENCES LOCATIONS_DIM (LID),
    FOREIGN KEY (FID) REFERENCES FACULTY_DIM (FID),
    FOREIGN KEY (CID) REFERENCES COURSE_CATALOGS_DIM (CID)
);

 * sqlite:///CourseDataWarehouse.db
Done.
Done.
Done.
Done.
Done.
Done.
Done.
Done.
Done.
Done.
Done.
Done.


[]

In [5]:
%%sql
SELECT * FROM  PROGRAMS_DIM
where program_code like "BA"
LIMIT 10

 * sqlite:///CourseDataWarehouse.db
Done.


[]

In [6]:
%%sql 


INSERT INTO PROGRAMS_DIM ( program_name, program_code)
SELECT DISTINCT  program_name, program_code
FROM CDDB.PROGRAMS;


INSERT INTO LOCATIONS_DIM (location ,BuildingName )
SELECT  location , BuildingName
FROM CDDB.LOCATION;


INSERT INTO FACULTY_DIM (instructor_fname , instructor_lname)
SELECT  DISTINCT instructor_fname , instructor_lname
FROM CDDB.FACULTY;


INSERT INTO COURSE_CATALOGS_DIM (Catalog_ID, credits, Prereqs, Coreqs, Fees, Description, Attributes)
SELECT catalog_ID, credits, prereqs, coreqs, fees, description, attributes
FROM CDDB.COURSE;



INSERT INTO COURSES_FACT (Catalog_ID , CRN, SEMESTER , YEAR , TITLE, SECTION, ACT, CAP,REM, TIMECODES, PID, LID, FID, CID)
SELECT DISTINCT CDDB.COURSE_OFFERING.Catalog_ID,  CDDB.CLASS_MEETINGS.CRN, CDDB.CLASS_MEETINGS.SEMESTER , CDDB.CLASS_MEETINGS.YEAR, CDDB.COURSE_OFFERING.title, CDDB.COURSE_OFFERING.SECTION, act, cap, rem, timecodes, PROGRAMS_DIM.PID, LOCATIONS_DIM.LID, FID,CDDB.COURSE.CID
FROM CDDB.COURSE_OFFERING
     JOIN CDDB.CLASS_MEETINGS USING  (COID)
    left JOIN LOCATIONS_DIM USING (LID)
     left JOIN CDDB.COURSE USING (CID)
    left JOIN PROGRAMS_DIM USING (PID)
    left JOIN FACULTY_DIM USING (FID)
    left JOIN COURSE_CATALOGS_DIM USING (CID);
    
    

    
   

 * sqlite:///CourseDataWarehouse.db
92 rows affected.
207 rows affected.
1104 rows affected.
11625 rows affected.
14713 rows affected.


[]

In [7]:
%%sql
SELECT FID, instructor_lname,instructor_fname,COURSES_FACT.Catalog_ID,program_name, Title ,sum(act), sum(cap), sum(rem) , YEAR,SEMESTER , COUNT(CRN) as COURSESTaught
FROM FACULTY_DIM
    left JOIN COURSES_FACT USING (FID)
     left JOIN COURSE_CATALOGS_DIM USING (CID)
    left  JOIN PROGRAMS_DIM USING (PID)
WHERE (instructor_lname like '%Huntley%')
GROUP BY title ,  YEAR,SEMESTER 

ORDER BY YEAR DESC


 * sqlite:///CourseDataWarehouse.db
Done.


[(275, 'Huntley', 'Christopher L.', 'BA0510', 'Business Analytics', 'Databases for Business Analytics', 68, 64, -4, 2019, 'Spring', 2),
 (275, 'Huntley', 'Christopher L.', 'OM0101', 'Operations Management', 'Operations Management', 53, 50, -3, 2019, 'Spring', 2),
 (275, 'Huntley', 'Christopher L.', 'IS0260', 'Information Systems', 'Database Systems', 24, 25, 1, 2018, 'Spring', 1),
 (275, 'Huntley', 'Christopher L.', 'OM0101', 'Operations Management', 'Operations Management', 49, 50, 1, 2018, 'Fall', 2),
 (275, 'Huntley', 'Christopher L.', 'BA0505', 'Business Analytics', 'Python for Business Analytics', 27, 20, -7, 2018, 'Fall', 1),
 (275, 'Huntley', 'Christopher L.', 'IS0240', 'Information Systems', 'Systems Analysis and Logical Design', 22, 25, 3, 2018, 'Spring', 1),
 (275, 'Huntley', 'Christopher L.', 'IS0320', 'Information Systems', 'Systems Design and Implementation', 20, 25, 5, 2018, 'Spring', 1),
 (275, 'Huntley', 'Christopher L.', 'IS0510', 'Information Systems', 'Databases for Business Analytics', 18, 20, 2, 2017, 'Fall', 1),
 (275, 'Huntley', 'Christopher L.', 'OM0101', 'Operations Management', 'Operations Management', 28, 29, 1, 2017, 'Spring', 1),
 (275, 'Huntley', 'Christopher L.', 'IS0505', 'Information Systems', 'Python for Business Analytics', 28, 20, -8, 2017, 'Fall', 1),
 (275, 'Huntley', 'Christopher L.', 'IS0240', 'Information Systems', 'Systems Analysis and Logical Design', 23, 25, 2, 2017, 'Fall', 1),
 (275, 'Huntley', 'Christopher L.', 'IS0240', 'Information Systems', 'Systems Analysis and Logical Design', 25, 25, 0, 2017, 'Spring', 1),
 (275, 'Huntley', 'Christopher L.', 'IS0320', 'Information Systems', 'Systems Design and Implementation', 7, 25, 18, 2017, 'Spring', 1),
 (275, 'Huntley', 'Christopher L.', 'IS0585C', None, 'Contemporary Topics: Database Systems for Business Analytics', 30, 40, 10, 2016, 'Fall', 2),
 (275, 'Huntley', 'Christopher L.', 'IS0585', 'Information Systems', 'Contemporary Topics: Information Systems and Data', 30, 40, 10, 2016, 'Spring', 2),
 (275, 'Huntley', 'Christopher L.', 'IS0135', 'Information Systems', 'Fundamentals of Web Design', 15, 25, 10, 2016, 'Fall', 1),
 (275, 'Huntley', 'Christopher L.', 'OM0101', 'Operations Management', 'Operations Management', 57, 58, 1, 2016, 'Spring', 2),
 (275, 'Huntley', 'Christopher L.', 'IS0240', 'Information Systems', 'Systems Analysis and Logical Design', 23, 25, 2, 2016, 'Fall', 1),
 (275, 'Huntley', 'Christopher L.', 'IS0135', 'Information Systems', 'Fundamentals of Web Design', 21, 25, 4, 2015, 'Fall', 1),
 (275, 'Huntley', 'Christopher L.', 'IS0100', 'Information Systems', 'Intro to Information Systems', 112, 116, 4, 2015, 'Fall', 4),
 (275, 'Huntley', 'Christopher L.', 'IS0320', 'Information Systems', 'Systems Design and Implementation', 13, 25, 12, 2015, 'Fall', 1),
 (275, 'Huntley', 'Christopher L.', 'IS0135', 'Information Systems', 'Fundamentals of Web Design', 26, 25, -1, 2014, 'Fall', 1),
 (275, 'Huntley', 'Christopher L.', 'IS0100', 'Information Systems', 'Intro to Information Systems', 26, 25, -1, 2014, 'Fall', 1),
 (275, 'Huntley', 'Christopher L.', 'IS0320', 'Information Systems', 'Systems Design and Implementation', 16, 25, 9, 2014, 'Fall', 1)]

In [8]:
%%sql
SELECT FID, instructor_lname,instructor_fname,COURSES_FACT.Catalog_ID,program_name, Title ,sum(act), sum(cap), sum(rem) , YEAR,SEMESTER , COUNT(CRN) as COURSESTaught
FROM FACULTY_DIM
    left JOIN COURSES_FACT USING (FID)
     left JOIN COURSE_CATALOGS_DIM USING (CID)
    left  JOIN PROGRAMS_DIM USING (PID)
WHERE (instructor_lname like '%Huntley%')
GROUP BY title ,  YEAR,SEMESTER 

ORDER BY YEAR DESC


 * sqlite:///CourseDataWarehouse.db
Done.


[(275, 'Huntley', 'Christopher L.', 'BA0510', 'Business Analytics', 'Databases for Business Analytics', 68, 64, -4, 2019, 'Spring', 2),
 (275, 'Huntley', 'Christopher L.', 'OM0101', 'Operations Management', 'Operations Management', 53, 50, -3, 2019, 'Spring', 2),
 (275, 'Huntley', 'Christopher L.', 'IS0260', 'Information Systems', 'Database Systems', 24, 25, 1, 2018, 'Spring', 1),
 (275, 'Huntley', 'Christopher L.', 'OM0101', 'Operations Management', 'Operations Management', 49, 50, 1, 2018, 'Fall', 2),
 (275, 'Huntley', 'Christopher L.', 'BA0505', 'Business Analytics', 'Python for Business Analytics', 27, 20, -7, 2018, 'Fall', 1),
 (275, 'Huntley', 'Christopher L.', 'IS0240', 'Information Systems', 'Systems Analysis and Logical Design', 22, 25, 3, 2018, 'Spring', 1),
 (275, 'Huntley', 'Christopher L.', 'IS0320', 'Information Systems', 'Systems Design and Implementation', 20, 25, 5, 2018, 'Spring', 1),
 (275, 'Huntley', 'Christopher L.', 'IS0510', 'Information Systems', 'Databases for Business Analytics', 18, 20, 2, 2017, 'Fall', 1),
 (275, 'Huntley', 'Christopher L.', 'OM0101', 'Operations Management', 'Operations Management', 28, 29, 1, 2017, 'Spring', 1),
 (275, 'Huntley', 'Christopher L.', 'IS0505', 'Information Systems', 'Python for Business Analytics', 28, 20, -8, 2017, 'Fall', 1),
 (275, 'Huntley', 'Christopher L.', 'IS0240', 'Information Systems', 'Systems Analysis and Logical Design', 23, 25, 2, 2017, 'Fall', 1),
 (275, 'Huntley', 'Christopher L.', 'IS0240', 'Information Systems', 'Systems Analysis and Logical Design', 25, 25, 0, 2017, 'Spring', 1),
 (275, 'Huntley', 'Christopher L.', 'IS0320', 'Information Systems', 'Systems Design and Implementation', 7, 25, 18, 2017, 'Spring', 1),
 (275, 'Huntley', 'Christopher L.', 'IS0585C', None, 'Contemporary Topics: Database Systems for Business Analytics', 30, 40, 10, 2016, 'Fall', 2),
 (275, 'Huntley', 'Christopher L.', 'IS0585', 'Information Systems', 'Contemporary Topics: Information Systems and Data', 30, 40, 10, 2016, 'Spring', 2),
 (275, 'Huntley', 'Christopher L.', 'IS0135', 'Information Systems', 'Fundamentals of Web Design', 15, 25, 10, 2016, 'Fall', 1),
 (275, 'Huntley', 'Christopher L.', 'OM0101', 'Operations Management', 'Operations Management', 57, 58, 1, 2016, 'Spring', 2),
 (275, 'Huntley', 'Christopher L.', 'IS0240', 'Information Systems', 'Systems Analysis and Logical Design', 23, 25, 2, 2016, 'Fall', 1),
 (275, 'Huntley', 'Christopher L.', 'IS0135', 'Information Systems', 'Fundamentals of Web Design', 21, 25, 4, 2015, 'Fall', 1),
 (275, 'Huntley', 'Christopher L.', 'IS0100', 'Information Systems', 'Intro to Information Systems', 112, 116, 4, 2015, 'Fall', 4),
 (275, 'Huntley', 'Christopher L.', 'IS0320', 'Information Systems', 'Systems Design and Implementation', 13, 25, 12, 2015, 'Fall', 1),
 (275, 'Huntley', 'Christopher L.', 'IS0135', 'Information Systems', 'Fundamentals of Web Design', 26, 25, -1, 2014, 'Fall', 1),
 (275, 'Huntley', 'Christopher L.', 'IS0100', 'Information Systems', 'Intro to Information Systems', 26, 25, -1, 2014, 'Fall', 1),
 (275, 'Huntley', 'Christopher L.', 'IS0320', 'Information Systems', 'Systems Design and Implementation', 16, 25, 9, 2014, 'Fall', 1)]

In [9]:
%%sql
SELECT instructor_lname,instructor_fname ,CatalogYear, COURSES_FACT.Catalog_ID,PROGRAMS_DIM.program_name,PROGRAMS_DIM.program_code, Title ,SECTION  ,CRN, SEMESTER , YEAR , ACT, CAP,REM, TIMECODES
FROM FACULTY_DIM
    left JOIN COURSES_FACT USING (FID)
    left JOIN COURSE_CATALOGS_DIM USING (CID)
    left JOIN CDDB.COURSE USING (CID)
   left  JOIN PROGRAMS_DIM USING (PID)
WHERE program_name is null
GROUP BY title ,  YEAR,SEMESTER 

ORDER BY YEAR DESC





 * sqlite:///CourseDataWarehouse.db
Done.


[('Drake', 'Ryan T.', None, 'PH0224', None, None, 'Critical Thinking', '01', 38856, 'Spring', 2019, 21, 20, -1, "['TF 0930am-1045am 01/22-04/30 CNS 104']"),
 ('Post', 'Jed Morgan', None, 'SA0140', None, None, 'Darkroom Photography', '01', 38773, 'Spring', 2019, 13, 15, 2, "['F 1100am-0130pm 01/22-04/30 LYL 20']"),
 ('Wills', 'Margaret A.', None, 'CO0350', None, None, 'Family Crisis Communication', '01', 38836, 'Spring', 2019, 19, 20, 1, "['MR 1230pm-0145pm 01/22-04/30 DMH 350']"),
 (' Iddins', 'Anne', None, 'CO0352', None, None, 'Global Mediated Activism', '01', 38837, 'Spring', 2019, 16, 17, 1, "['M 0800am-1030am 01/22-04/30 DMH 148']"),
 ('Vinekar', 'Vishnu V.', None, 'IS0235', None, None, 'Python Apps for Busn Analytics', '01', 39010, 'Spring', 2019, 10, 20, 10, "['TF 0200pm-0315pm 01/22-04/30 DSB 2109A']"),
 ('Biardi', 'James E.', None, 'BI0399M', None, None, 'Senior Capstone Seminar: Conservation Biology', '01', 38705, 'Spring', 2019, 10, 10, 0, "['MR 1100am-1215pm 01/22-04/30 NHS 210']"),
 ('Henkel', 'Linda A.', None, 'PY0281G', None, None, 'Special Topics: Aging and Cognition', '01', 38821, 'Spring', 2019, 4, 15, 11, "['MR 0330pm-0445pm 01/22-04/30 BNW 341']"),
 (' Horan', 'Sean', None, 'CO0559D', None, None, 'Special Topics: Communication Training and Development', '01', 38841, 'Spring', 2019, 12, 13, 1, "['T 0630pm-0900pm 01/22-05/10 DMH 348']"),
 ('Ramsey', 'Mark D.', None, 'SW0482G', None, None, 'Special Topics: Cybersecurity', '01', 38906, 'Spring', 2019, 7, 5, -2, "['MW 0500pm-0615pm 01/22-04/30 BNW 131']"),
 (' Hardy', 'Clarence', None, 'RS0299D', None, None, 'Special Topics: Martin Luther King, Jr.', '01', 38921, 'Spring', 2019, 18, 25, 7, "['MR 0200pm-0315pm 01/22-04/30 CNS 206']"),
 ('Hollingsworth', 'David W.', None, 'PY0281H', None, None, 'Special Topics: Psychology of Diversity', '01', 38822, 'Spring', 2019, 22, 22, 0, "['MR 1230pm-0145pm 01/22-04/30 DMH 148']"),
 (' Robert', 'Tracey', None, 'NS0385A', None, None, 'Special Topics: Spirituality in Nursing', '01', 39032, 'Spring', 2019, 2, 10, 8, "['U 0100pm-0230pm 03/03-04/07 NHS 411']"),
 ('Cavallo', 'James P.', None, 'CS0201', None, None, 'Technical Skills for Liberal Arts Majors', '01', 38880, 'Spring', 2019, 0, 20, 20, "['MR 0930am-1045am 01/22-04/30 CNS 301']"),
 (' Lischinsky', 'Marissa', None, 'FE0002', None, None, 'Transfer Student Experience', '01', 39064, 'Spring', 2019, 13, 20, 7, "['W 1000am-1050am 01/22-04/30 NHS 410']"),
 (' Speretta', 'Mirco', None, 'CS0320', None, None, 'Visual Analytics', '01', 39029, 'Spring', 2019, 7, 7, 0, "['F 0500pm-0730pm 01/22-04/30 BNW 166']"),
 ('Heller', 'Nicole Elizabeth', None, 'FE0001', None, None, 'First Year Experience', '01', 74058, 'Fall', 2018, 19, 35, 16, "['T 0200pm-0315pm 09/04-12/10 DMH 349']"),
 (' Yu', 'Haozhe', None, 'FE0001', None, None, 'First Year Experience', '01', 35505, 'Spring', 2018, 14, 20, 6, "['T 1100am-1150am 01/16-05/01 NHS 411']"),
 (' Fine', 'Benjamin', None, 'MA0495C', None, None, 'Special Topics: Cryptography', '01', 58420, 'Summer', 2018, 12, 12, 0, "['MW 0600pm-0900pm 07/09-08/18 BNW 341']"),
 ('Schlichting', 'Kurt C.', None, 'AS0405A', None, None, 'Special Topics: Study Away: Newport, Rhode Island: "A Lively Experiment"', '01', 58339, 'Summer', 2018, 6, 15, 9, "['R 0630pm-0830pm 05/31-06/14 DMH 331', 'RFSU TBA 06/21-06/24 BY ARR ']"),
 (' Patton', 'Martha Jane', None, 'PO0190E', None, None, 'Special Topics: Turkey: A Nation of Contradictions in Turmoil', '01', 75845, 'Fall', 2018, 15, 25, 10, "['T 0500pm-0730pm 09/04-12/10 CNS 9']"),
 (' Horan', 'Sean', None, 'CO0559C', None, None, 'Special Topics: Work-Life Intersections', '01', 75982, 'Fall', 2018, 14, 15, 1, "['M 0630pm-0900pm 09/04-12/17 DMH 131']"),
 ('Heller', 'Nicole Elizabeth', None, 'FE0002', None, None, 'Transfer Student Experience', '01', 75473, 'Fall', 2018, 11, 30, 19, "['M 0200pm-0250pm 09/04-12/10 BNW 335']"),
 ('Elliott', 'Joshua C.', None, 'MD0099', None, None, 'Comprehensive Exam', '02', 57432, 'Summer', 2017, 1,

In [ ]:
('Fall2014','2014_2015'),
('Winter2015','2014_2015'),
('Spring2015','2014_2015'),
('Summer2015','2014_2015'),

('Fall2015','2015_2016'),
('Winter2016','2015_2016'),
('Spring2016','2015_2016'),
('Summer2016','2015_2016'),

('Fall2016','2016_2017'),
('Winter2017','2016_2017'),
('Spring2017','2016_2017'),
('SpringBreak2017','2016_2017'),
('Summer2017','2016_2017'),

('Fall2017','2017_2018'),
('Winter2018','2017_2018'),
('Spring2018','2017_2018'),
('Summer2018','2017_2018'),

('Fall2018','2018_2019'),
('Winter2019','2018_2019'),
('Spring2019','2018_2019')

In [42]:
%%sql
SELECT YEAR,SEMESTER ,SEMESTER|| '' ||YEAR as term,CatalogYear, COURSES_FACT.Catalog_ID,PROGRAMS_DIM.program_name,PROGRAMS_DIM.program_code,Title, CDDB.COURSE.credits, COURSE_CATALOGS_DIM.Prereqs, COURSE_CATALOGS_DIM.Coreqs, COURSE_CATALOGS_DIM.Fees,  COURSE_CATALOGS_DIM.Attributes, COURSE_CATALOGS_DIM.Description
FROM FACULTY_DIM
    left JOIN COURSES_FACT USING (FID)
    left JOIN COURSE_CATALOGS_DIM USING (CID)
    left JOIN CDDB.COURSE USING (CID)
   left  JOIN PROGRAMS_DIM USING (PID)
WHERE program_name is NULL 




 * sqlite:///CourseDataWarehouse.db
Done.


[(2014, 'Fall', 'Fall2014', None, 'AC 0011', None, None, 'Introduction to Financial Accounting', None, None, None, None, None, None),
 (2014, 'Fall', 'Fall2014', None, 'AC 0011', None, None, 'Introduction to Financial Accounting', None, None, None, None, None, None),
 (2014, 'Fall', 'Fall2014', None, 'AC 0011', None, None, 'Introduction to Financial Accounting', None, None, None, None, None, None),
 (2015, 'Fall', 'Fall2015', None, 'AC 0011', None, None, 'Introduction to Financial Accounting', None, None, None, None, None, None),
 (2015, 'Fall', 'Fall2015', None, 'AC 0011', None, None, 'Introduction to Financial Accounting', None, None, None, None, None, None),
 (2015, 'Fall', 'Fall2015', None, 'AC 0011', None, None, 'Introduction to Financial Accounting', None, None, None, None, None, None),
 (2016, 'Fall', 'Fall2016', None, 'AC 0500', None, None, 'Accounting Information for Decision-Making', None, None, None, None, None, None),
 (2016, 'Fall', 'Fall2016', None, 'AC 0500', None, None, 'Accounting Information for Decision-Making', None, None, None, None, None, None),
 (2016, 'Fall', 'Fall2016', None, 'AC 0400', None, None, 'Introduction to Accounting', None, None, None, None, None, None),
 (2016, 'Fall', 'Fall2016', None, 'AC 0400', None, None, 'Introduction to Accounting', None, None, None, None, None, None),
 (2016, 'Fall', 'Fall2016', None, 'AC 0011', None, None, 'Introduction to Financial Accounting', None, None, None, None, None, None),
 (2015, 'Spring', 'Spring2015', None, 'AC 0520', None, None, 'International Accounting', None, None, None, None, None, None),
 (2015, 'Spring', 'Spring2015', None, 'AC 0012', None, None, 'Introduction to Management Accounting', None, None, None, None, None, None),
 (2015, 'Spring', 'Spring2015', None, 'AC 0012', None, None, 'Introduction to Management Accounting', None, None, None, None, None, None),
 (2016, 'Spring', 'Spring2016', None, 'AC 0012', None, None, 'Introduction to Management Accounting', None, None, None, None, None, None),
 (2016, 'Spring', 'Spring2016', None, 'AC 0012', None, None, 'Introduction to Management Accounting', None, None, None, None, None, None),
 (2016, 'Spring', 'Spring2016', None, 'AC 0012', None, None, 'Introduction to Management Accounting', None, None, None, None, None, None),
 (2016, 'Spring', 'Spring2016', None, 'AC 0012', None, None, 'Introduction to Management Accounting', None, None, None, None, None, None),
 (2017, 'Spring', 'Spring2017', None, 'AC 0500', None, None, 'Accounting Information for Decision-Making', None, None, None, None, None, None),
 (2017, 'Spring', 'Spring2017', None, 'AC 0012', None, None, 'Introduction to Management Accounting', None, None, None, None, None, None),
 (2017, 'Spring', 'Spring2017', None, 'AC 0012', None, None, 'Introduction to Management Accounting', None, None, None, None, None, None),
 (2017, 'Summer', 'Summer2017', None, 'AC 0400', None, None, 'Introduction to Accounting', None, None, None, None, None, None),
 (2014, 'Fall', 'Fall2014', None, 'AC 0011', None, None, 'Introduction to Financial Accounting', None, None, None, None, None, None),
 (2014, 'Fall', 'Fall2014', None, 'AC 0011', None, None, 'Introduction to Financial Accounting', None, None, None, None, None, None),
 (2014, 'Fall', 'Fall2014', None, 'AC 0011', None, None, 'Introduction to Financial Accounting', None, None, None, None, None, None),
 (2015, 'Fall', 'Fall2015', None, 'AC 0203', None, None, 'Intermediate Accounting I', None, None, None, None, None, None),
 (2015, 'Fall', 'Fall2015', None, 'AC 0011', None, None, 'Introduction to Financial Accounting', None, None, None, None, None, None),
 (2015, 'Fall', 'Fall2015', None, 'AC 0011', None, None, 'Introduction to Financial Accounting', None, None, None, None, None, None),
 (2016, 'Fall', 'Fall2016', None, 'AC 0011', None, None, 'Introduction to Financial Accounting', None, None, None, None, None, None),
 (2016, 'Fall', 'Fall2016', None, 'AC 0011', None, None, 'Introduction to Financial Accounting', 

In [65]:

missing_df = _.DataFrame()






YEAR SEMESTER        term CatalogYear Catalog_ID program_name  \
0     2014.0     Fall    Fall2014        None    AC 0011         None   
1     2014.0     Fall    Fall2014        None    AC 0011         None   
2     2014.0     Fall    Fall2014        None    AC 0011         None   
11    2015.0   Spring  Spring2015        None    AC 0520         None   
12    2015.0   Spring  Spring2015        None    AC 0012         None   
...      ...      ...         ...         ...        ...          ...   
8572  2015.0   Summer  Summer2015        None    NS 0605         None   
8573  2015.0   Summer  Summer2015        None  NSAN 0678         None   
8576  2015.0   Summer  Summer2015        None    SE 0400         None   
8577  2015.0   Summer  Summer2015        None    SE 0534         None   
8578  2015.0   Summer  Summer2015        None    SL 0439         None   

     program_code                                              Title credits  \
0            None               Introduction to Financial Accounting    None   
1            None               Introduction to Financial Accounting    None   
2            None               Introduction to Financial Accounting    None   
11           None                           International Accounting    None   
12           None              Introduction to Management Accounting    None   
...           ...                                                ...     ...   
8572         None                         Advanced Healthcare Policy    None   
8573         None  Regional Anesthesia and Pain Management in Cli...    None   
8576         None  Augmentative Alternative Communications and As...    None   
8577         None  Sklll Development for Individualized Education...    None   
8578         None  Methods of Foreign Language Teaching for Eleme...    None   

     Prereqs Coreqs  Fees Attributes Description  
0       None   None  None       None        None  
1       None   None  None       None        None  
2       None   None  None       None        None  
11      None   None  None       None        None  
12      None   None  None       None        None  
...      ...    ...   ...        ...         ...  
8572    None   None  None       None        None  
8573    None   None  None       None        None  
8576    None   None  None       None        None  
8577    None   None  None       None        None  
8578    None   None  None       None        None  

[2780 rows x 14 columns]

In [90]:
term_lst= ['Fall2016','Winter2017' , 'Spring2017' ,'Summer2017'  ,'SpringBreak2017']



df = missing_df[missing_df.term.isin(term_lst)]

df = df[df.duplicated(['Catalog_ID'])==False].sort_values('Catalog_ID')

df['CatalogYear'] = '2016_2017'
df.to_csv('CourseCatalog2016_2017.csv')




In [13]:
%%sql
SELECT DISTINCT COUNT(CRN), COUNT(CID), COUNT(CRN)
FROM COURSES_FACT;

 * sqlite:///CourseDataWarehouse.db
Done.


[(25525, 25525, 25525)]

In [14]:
# do we have enghe sections for students

In [15]:
%%sql

SELECT  Title , count(*) , count(FID) , sum(Act) ,sum(Cap), sum(Rem)  , YEAR 
FROM COURSES_FACT
left JOIN PROGRAMS_DIM USING (PID)
WHERE  Catalog_ID like "%IS%"
group by Title , YEAR 
having sum(Rem) <0
order by year desc
    

 * sqlite:///CourseDataWarehouse.db
Done.


[('Introduction to Information Systems', 7, 7, 181, 175, -6, 2019),
 ('Data Mining and Applications', 2, 2, 47, 45, -2, 2018),
 ('Fundamentals of Business Analytics', 2, 2, 55, 50, -5, 2017),
 ('Python for Business Analytics', 1, 1, 28, 20, -8, 2017),
 ('Contemporary Topics: Business Analytics with Spreadsheets', 1, 1, 1, 0, -1, 2016),
 ('Fundamentals of Web Design', 1, 1, 26, 25, -1, 2014),
 ('Intro to Information Systems', 10, 10, 237, 227, -10, 2014)]

In [24]:
%%sql

SELECT *
FROM COURSES_FACT
JOIN PROGRAMS_DIM USING (PID)
WHERE YEAR = 2017 and program_name like "%information%"
group by Title 


 * sqlite:///CourseDataWarehouse.db
Done.


[(8010, 32108, 'Spring', 2017, 'Business Analytics and Big Data Mgmt', '01', 17, 25, 8, "['R 0630pm-0930pm 03/08-04/26 DSB 114', 'S 0830am-0430pm 03/25-03/25 DSB 107', 'S 0830am-0430pm 04/08-04/08 DSB 107', 'S 0830am-0430pm 04/29-04/29 DSB 107']", 52, 92, 619, 'IS 0550', 'IS', 'Information Systems'),
 (13456, 32107, 'Spring', 2017, 'Data Mining and Business Intelligence', '01', 19, 25, 6, "['W 0630pm-0930pm 01/17-05/12 DSB 114']", 52, 92, 619, 'IS 0540', 'IS', 'Information Systems'),
 (923, 71341, 'Fall', 2017, 'Database Systems', '01', 23, 25, 2, "['TF 0330pm-0445pm 09/05-12/11 DSB 112']", 52, 7, 273, 'IS 0260', 'IS', 'Information Systems'),
 (1152, 72914, 'Fall', 2017, 'Databases for Business Analytics', '01', 18, 20, 2, "['T 0630pm-0930pm 10/31-12/12 DSB 115', 'S 0830am-0430pm 11/04-11/04 DSB 115', 'S 0830am-0430pm 11/18-11/18 DSB 115', 'S 0830am-0430pm 12/09-12/09 DSB 115']", 52, 9, 275, 'IS 0510', 'IS', 'Information Systems'),
 (924, 71287, 'Fall', 2017, 'E-Business Applications', '01', 19, 20, 1, "['W 1100am-0130pm 09/05-12/11 DSB 2109A']", 52, 10, 274, 'IS 0310', 'IS', 'Information Systems'),
 (7909, 31734, 'Spring', 2017, 'Fundamentals of Business Analytics', '01', 23, 25, 2, "['MR 0930am-1045am 01/17-05/02 CNS 301']", 52, 68, 431, 'IS 0210', 'IS', 'Information Systems'),
 (920, 71929, 'Fall', 2017, 'Fundamentals of Web Design', '01', 17, 20, 3, "['MR 0330pm-0445pm 09/05-12/11 DSB 109']", 52, 8, 274, 'IS 0135', 'IS', 'Information Systems'),
 (8008, 32651, 'Spring', 2017, 'Information Systems and Database Management', '01', 15, 25, 10, "['R 0630pm-0930pm 01/17-03/02 DSB 115', 'S 0830am-0430pm 01/28-01/28 DSB 115', 'S 0830am-0430pm 02/11-02/11 DSB 115', 'S 0830am-0430pm 02/25-02/25 DSB 115']", 52, 9, 619, 'IS 0500', 'IS', 'Information Systems'),
 (857, 71166, 'Fall', 2017, 'Introduction to Information Systems', '01', 30, 28, -2, "['TF 0930am-1045am 09/05-12/11 DSB 105']", 52, 1, 273, 'IS 0100', 'IS', 'Information Systems'),
 (8009, 32647, 'Spring', 2017, 'Project Management', '01', 14, 25, 11, "['T 0630pm-0930pm 03/07-04/25 DSB 105', 'S 0830am-0430pm 03/25-03/25 DSB 105', 'S 0830am-0430pm 04/08-04/08 DSB 105', 'S 0830am-0430pm 04/22-04/22 DSB 105']", 52, 1, 278, 'IS 0520', 'IS', 'Information Systems'),
 (1151, 72913, 'Fall', 2017, 'Python for Business Analytics', '01', 28, 20, -8, "['T 0630pm-0930pm 09/05-10/17 DSB 115', 'S 0830am-0430pm 09/09-09/09 DSB 115', 'S 0830am-0430pm 09/23-09/23 DSB 115', 'S 0830am-0430pm 10/07-10/07 DSB 115']", 52, 9, 275, 'IS 0505', 'IS', 'Information Systems'),
 (922, 71153, 'Fall', 2017, 'Systems Analysis and Logical Design', '01', 23, 25, 2, "['TF 1230pm-0145pm 09/05-12/11 DSB 110A']", 52, 3, 275, 'IS 0240', 'IS', 'Information Systems'),
 (7914, 32646, 'Spring', 2017, 'Systems Design and Implementation', '01', 7, 25, 18, "['W 0200pm-0430pm 01/17-05/02 DSB 2109A']", 52, 10, 275, 'IS 0320', 'IS', 'Information Systems')]

In [29]:
%%sql
vacuum; 

 * sqlite:///CourseDataWarehouse.db
Done.


[]

In [17]:
import pandas as pd
#https://datatofish.com/create-database-python-using-sqlite3/
from sqlalchemy import create_engine

engine = create_engine("sqlite:///CourseDataWarehouse.db")
#pick a table to load into a df

#load the table into a df  and give a condition( where, join)
query = ''' SELECT instructor_lname,instructor_fname,CatalogYear,  COURSES_FACT.Catalog_ID,program_name,program_code, Title ,SECTION  ,CRN, SEMESTER , YEAR , ACT, CAP,REM, TIMECODES
FROM FACULTY_DIM
    left JOIN COURSES_FACT USING (FID)
    left JOIN COURSE_CATALOGS_DIM USING (CID)
    left JOIN CDDB.COURSE USING (CID)
   left  JOIN PROGRAMS_DIM USING (PID)
   left  JOIN PROGRAMS_DIM USING (PID)
WHERE program_name is null
GROUP BY title ,  YEAR,SEMESTER 

ORDER BY YEAR DESC'''
tables = pd.read_sql_query(query,engine)
tables.shape

OperationalError: (sqlite3.OperationalError) no such column: CourseData.db
[SQL: ATTACH CourseData.db AS CDDB ; SELECT instructor_lname,instructor_fname,CatalogYear,  COURSES_FACT.Catalog_ID,program_name,program_code, Title ,SECTION  ,CRN, SEMESTER , YEAR , ACT, CAP,REM, TIMECODES
FROM FACULTY_DIM
    left JOIN COURSES_FACT USING (FID)
    left JOIN COURSE_CATALOGS_DIM USING (CID)
    left JOIN CDDB.COURSE USING (CID)
   left  JOIN PROGRAMS_DIM USING (PID)
   left  JOIN PROGRAMS_DIM USING (PID)
WHERE program_name is null
GROUP BY title ,  YEAR,SEMESTER 

ORDER BY YEAR DESC]
(Background on this error at: http://sqlalche.me/e/e3q8)

In [15]:
tables

instructor_lname instructor_fname Catalog_ID program_name program_code  \
0            Lakeland          Paul F.    RS 0268         None         None   
1             Cassidy         Kevin J.    PO 0233         None         None   
2             Bagirov            Feyzi    BA 0540         None         None   
3                  Li            Danke    HI 0102         None         None   
4                Rusu        Amalia I.   CS 0351L         None         None   
...               ...              ...        ...          ...          ...   
4365         LoMonaco        Martha S.    TA 0111         None         None   
4366            Huber         Sonya R.   ENW 0340         None         None   
4367        Silverman         Francine   ENW 0320         None         None   
4368         Humphrey          Hugh M.    RS 0220         None         None   
4369          Berwick          Tara M.       None         None         None   

                                  Title SECTION      CRN SEMESTER    YEAR  \
0             American Catholic History      01  38873.0   Spring  2019.0   
1            American Political Thought      01  38728.0   Spring  2019.0   
2                 Business Intelligence      01  39007.0   Spring  2019.0   
3              China, Japan, and Europe      01  38788.0   Spring  2019.0   
4     Computer Science Junior Clinic II      01  38886.0   Spring  2019.0   
...                                 ...     ...      ...      ...     ...   
4365    World Theatre: 1800 to Tomorrow       A  73009.0     Fall  2014.0   
4366              World of Publishing I       A  71658.0     Fall  2014.0   
4367          Writing the Feature Story       A  71099.0     Fall  2014.0   
4368                   Writings of Paul       A  72975.0     Fall  2014.0   
4369                               None    None      NaN     None     NaN   

       Act   Cap   Rem                                          timecodes  
0     25.0  25.0   0.0           ['TF 1100am-1215pm 01/22-04/30 CNS 304']  
1     22.0  25.0   3.0           ['MR 1100am-1215pm 01/22-04/30 CNS 103']  
2     30.0  30.0   0.0            ['R 0630pm-0930pm 03/25-05/10 DSB 115']  
3     25.0  25.0   0.0           ['TF 0200pm-0315pm 01/22-04/30 DMH 347']  
4      7.0  20.0  13.0            ['R 0930am-1020am 01/22-04/30 BNW 131']  
...    ...   ...   ...                                                ...  
4365  12.0  14.0   2.0  ['MR 1230pm-0120pm 09/02-12/08 DMH 149', 'W 12...  
4366  12.0  15.0   3.0           ['TF 1230pm-0145pm 09/02-12/08 DMH 131']  
4367   7.0  15.0   8.0            ['T 0700pm-0930pm 09/02-12/08 CNS 304']  
4368  25.0  25.0   0.0           ['TF 1230pm-0145pm 09/02-12/08 DMH 349']  
4369   NaN   NaN   NaN                                               None  

[4370 rows x 14 columns]

In [11]:
tables.to_csv("missing_Catalog_ID_all_info.csv")

In [31]:




import pandas as pd
#https://datatofish.com/create-database-python-using-sqlite3/
from sqlalchemy import create_engine

engine = create_engine("sqlite:///CourseDataWarehouse.db")
#pick a table to load into a df

#load the table into a df  and give a condition( where, join)
query = '''SELECT COURSES_FACT.Catalog_ID,program_name,program_code,Title, credits, Prereqs, Coreqs, Fees,  Attributes Description
FROM FACULTY_DIM
    left JOIN COURSES_FACT USING (FID)
    left JOIN COURSE_CATALOGS_DIM USING (CID)
   left  JOIN PROGRAMS_DIM USING (PID)
WHERE program_name is null
GROUP BY title ,  YEAR,SEMESTER 

ORDER BY YEAR DESC'''
tables = pd.read_sql_query(query,engine)
tables.shape

(1, 8)

In [10]:
#tables.to_csv("missing_Catalog_ID_all_info4.csv")